##### Cleaning and pre-proc

In [6]:
import pandas as pd
df = pd.read_csv('main_data_copy.csv')


def is_utf8(row):
    try:
        row.to_string().encode('utf-8')
        return True
    except UnicodeEncodeError:
        return False


df = df[df.apply(is_utf8, axis=1)]

for row in df.iterrows():
    print(row[1].to_string().encode('utf-8'))

# df['topic_categories'] = df['topic_categories'].str.replace(r'^.*wiki/', '', regex=True)

df.dropna()

df = df.loc[:, ['id', 'title', 'description', 'topic_categories', 'category', 'thumbnail']]
df.to_csv('filtered_main_data_copy.csv', index=False)

b'id                                                        B0RVWU_nROk\ntitle                                 I used a flip phone for 30 days\nview                                                           138040\nchannel_sub                                                   3020000\nview_to_sub                                                  0.045709\nlike                                                          11646.0\ndislike                                                         142.0\ncomment                                                        1304.0\nlength                                                       PT13M14S\ndescription         Go check out my habits course: https://slowgro...\ndimension                                                          2d\ndefinition                                                         hd\ncaption                                                         False\npublished_at                                     2020-12-30T20:00:05Z\ntags

In [7]:
distracting_keywords = [
    "funny", "prank", "game", "meme", "entertainment", "fail", "drama", 
    "reaction", "challenge", "vlog", "epic", "weird", "random", "amazing", "slander", "brainrot", "gyatt", "skibidi", "toilet", "skibidi toilet", "skibidi toilet challenge", "skibidi toilet challenge brainrot", "skibidi toilet challenge brainrot gyatt", "skibidi toilet challenge brainrot gyatt slander", "skibidi toilet challenge brainrot gyatt slander epic", "skibidi toilet challenge brainrot gyatt slander epic fail", "skibidi toilet challenge brainrot gyatt slander epic fail meme", "skibidi toilet challenge brainrot gyatt slander epic fail meme vlog", "skibidi toilet challenge brainrot gyatt slander epic fail meme vlog reaction", "skibidi toilet challenge brainrot gyatt slander epic fail meme vlog reaction drama", "skibidi toilet challenge brainrot gyatt"
]

def is_distracting(row):
    text = str(row['title']) + " " + str(row.get('description', ''))
    for keyword in distracting_keywords:
        if keyword in text.lower():
            return 1  # Distracting
    
    if row['category'] in [24, 20, 17]:  # Example: Entertainment, Gaming, etc.
        return 1  # Distracting
    
    # else non distracting
    return 0

df['distracting'] = df.apply(is_distracting, axis=1)

df['distracting'].value_counts(), df.head()
df.to_csv('filtered_main_data_copy.csv', index=False)


In [8]:
import pandas as pd
from sklearn.model_selection import train_test_split
from sklearn.linear_model import LogisticRegression
from sklearn.metrics import accuracy_score

df = pd.read_csv('filtered_main_data_copy.csv')

df['title_numeric'] = df['title'].astype('category').cat.codes
df['description_numeric'] = df['description'].astype('category').cat.codes
df['topic_categories_numeric'] = df['topic_categories'].astype('category').cat.codes


X = df[['title_numeric', 'description_numeric', 'topic_categories_numeric']]
y = df['distracting']

X_train, X_test, y_train, y_test = train_test_split(
    X, y, test_size=0.2, random_state=42)

model = LogisticRegression()
model.fit(X_train, y_train)

y_pred = model.predict(X_test)

accuracy = accuracy_score(y_test, y_pred)
print(f'Accuracy: {accuracy:.2f}')

Accuracy: 0.59


In [31]:
def predict_distracting(title, description, topic_categories):
    # Convert input to numeric categories
    title_numeric = pd.Series([title]).astype('category').cat.codes[0]
    description_numeric = pd.Series([description]).astype('category').cat.codes[0]
    topic_categories_numeric = pd.Series([topic_categories]).astype('category').cat.codes[0]
    
    # Create a DataFrame for the input
    input_data = pd.DataFrame({
        'title_numeric': [title_numeric],
        'description_numeric': [description_numeric],
        'topic_categories_numeric': [topic_categories_numeric]
    })
    
    # Predict using the trained model
    prediction = model.predict(input_data)
    
    return 'Distracting' if prediction[0] == 1 else 'Not Distracting'

# Example usage
title = "Spider-Man but he has brainrot"
description = """
What if Peter Parker was Gen Alpha?\n\nIntro Music: https://www.youtube.com/watch?v=ezjAKF1bHcE",
"""
topic_categories = """https://en.wikipedia.org/wiki/Entertainment",
          "https://en.wikipedia.org/wiki/Film"""
result = predict_distracting(title, description, topic_categories)
print(result)

Not Distracting


In [ ]:
import requests
import pandas as pd


def get_input_data():
    response = requests.get('http://localhost:5000/get_input_data')
    if response.status_code == 200:
        print(response.json())
        return response.json()
    else:
        print("No data available")
        return None

data = get_input_data()
if data:
    videoInput = pd.DataFrame([data])
    print(videoInput)
else:
    videoInput = pd.DataFrame()
    
    
title = videoInput.get('title', [''])[0]
description = videoInput.get('description', [''])[0]
topic_categories = videoInput.get('topic_categories', [''])[0]

result = predict_distracting(title, description, topic_categories)
print(result)

# result = predict_distracting(videoInput['title'][0], videoInput['description'][0], videoInput['topic_categories'][0])
# print(result)



In [24]:
videoInput

category          description          title
0  Example Category  Example Description  Example Title

None


In [ ]:
%tb

In [ ]:
"""
How to use git pull --rebase to keep your team's commit history clean.

Command for creating the 'git pr' alias (so you can copy-paste):

git config --global alias.pr "pull --rebase"

Thank you to Bruno Paulino, Ben Freundorfer, and Jonas Geiler for reviewing drafts of this video and their feedback!

Video Contents:
0:00 - Never use git pull
0:43 - Why not git pull?
1:40 - Using git pull --rebase
2:11 - Dealing with conflicts
2:52 - Final tips and summary

LEGAL DISCLAIMER

Everything here is for informational purposes only. All non-licensed clips used for fair use commentary, criticism, and educational purposes.  See Hosseinzadeh v. Klein, 276 F.Supp.3d 34 (S.D.N.Y. 2017); Equals Three, LLC v. Jukin Media, Inc., 139 F. Supp. 3d 1094 (C.D. Cal. 2015).
"""

'\nHow to use git pull --rebase to keep your team\'s commit history clean.\n\nCommand for creating the \'git pr\' alias (so you can copy-paste):\n\ngit config --global alias.pr "pull --rebase"\n\nThank you to Bruno Paulino, Ben Freundorfer, and Jonas Geiler for reviewing drafts of this video and their feedback!\n\nVideo Contents:\n0:00 - Never use git pull\n0:43 - Why not git pull?\n1:40 - Using git pull --rebase\n2:11 - Dealing with conflicts\n2:52 - Final tips and summary\n\nLEGAL DISCLAIMER\n\nEverything here is for informational purposes only. All non-licensed clips used for fair use commentary, criticism, and educational purposes.  See Hosseinzadeh v. Klein, 276 F.Supp.3d 34 (S.D.N.Y. 2017); Equals Three, LLC v. Jukin Media, Inc., 139 F. Supp. 3d 1094 (C.D. Cal. 2015).\n'